In [1]:
#Importa as bibliotecas necessárias
import pandas as pd
import numpy as np
import random
from datetime import timedelta
from datetime import date

In [2]:
#Cria uma base fictícia de colaboradores, representados por suas matrículas únicas
base_ficticia = pd.DataFrame()
#Seleciona uma amostra de códigos de matrícula com quantia equivalente ao número de colaboradores disponíveis
base_ficticia['matricula'] = random.sample(range(100,999),50)

In [3]:
'''
Para cada um dos colaboradores (matrícula), vamos criar eventos aleatórios de 4 tipos:
- On: momento em que o colaborador realiza o login no sistema
- Start: evento que indica o início de alguma atividade
- Pausa: evento que indica uma paralisação das atividades
- Off: evento que indica que o colaborador não está mais no sistema (deslogou) 
As regras para análise são as seguintes:
1) Após um login, ou seja, status "on", o colaborador deve voluntariamente clicar em "start" para iniciar as atividades
2) Logo após um login, não é possível ocorrer o status "pausa", já que este é definido automaticamente pelo sistema após o login
3) Logo após um "start", não é possível que ocorra um status "on"
4) Logo após um status "pausa", não é possível que ocorra um status "on"
5) Logo após um status "off", apenas é possível que ocorra um status "on"
'''

#Criando os eventos possívels
eventos = ['on','start','pausa','off']
#Cria uma função que define o número de eventos em um dia específico, bem como quais são eles
def cria_eventos():
  num_eventos = random.randint(0,20)
  lista_eventos = []
  evento = None
  for i in range(num_eventos):
    if i == 0:
      #evento = random.sample(eventos,1)[0]
      evento = 'on'
      lista_eventos.append(evento)
    elif evento == 'on':
      novos_eventos = ['start','off']
      evento = random.sample(novos_eventos,1)[0]
      lista_eventos.append(evento)
    elif evento == 'start':
      novos_eventos = ['pausa','off']
      evento = random.sample(novos_eventos,1)[0]
      lista_eventos.append(evento)
    elif evento == 'pausa':
      novos_eventos = ['start','off']
      evento = random.sample(novos_eventos,1)[0]
      lista_eventos.append(evento)
    elif evento == 'off':
      evento = 'on'
      lista_eventos.append(evento)
    
  lista_momentos = random.sample(range(0,86399),num_eventos)
  #lista_momentos = [(pd.to_datetime('00:00')+timedelta(seconds=momento)).time() for momento in lista_momentos]
  lista_momentos.sort()

  return lista_eventos,lista_momentos

eventos_colaboradores = {}

for matricula in base_ficticia['matricula']:
  eventos_colaboradores[matricula] = cria_eventos()

In [4]:
def tempo_logado(evento,espelho_evento,hora,espelho_hora):
  if espelho_evento != 'on':
    tempo_logado = espelho_hora - hora
  else:
    #tempo_logado = pd.to_datetime('00:00').time()
    tempo_logado = 0
  
  return tempo_logado

def tempo_produtivo(evento,espelho_evento,hora,espelho_hora):
  if evento == 'start' and espelho_evento != 'on':
    tempo_produtivo = espelho_hora - hora
  else: 
    #tempo_produtivo = pd.to_datetime('00:00').time()
    tempo_produtivo = 0

  return tempo_produtivo

#df_temp = pd.DataFrame({'evento':['start','pausa'],
#                       'hora':[pd.to_datetime('00:00:00').time(),pd.to_datetime('23:59:59').time()]})
df_temp = pd.DataFrame({'evento':['start','off'],
                       'hora':[0,86399]})

for key in eventos_colaboradores:
  df_eventos = pd.DataFrame({'evento':eventos_colaboradores[key][0],
                             'hora':eventos_colaboradores[key][1]})
  df_eventos = pd.concat([df_eventos,df_temp],axis=0)
  df_eventos.sort_values(by='hora',inplace = True)
  df_eventos.reset_index(drop = True,inplace = True)

  df_eventos['espelho_evento'] = list(df_eventos['evento'][1:])+[None]
  df_eventos['espelho_hora'] = list(df_eventos['hora'][1:])+[None]

  df_eventos['tempo_logado'] = list(map(tempo_logado,df_eventos['evento'],df_eventos['espelho_evento'],
                                        df_eventos['hora'],df_eventos['espelho_hora']))
  df_eventos['tempo_produtivo'] = list(map(tempo_produtivo,df_eventos['evento'],df_eventos['espelho_evento'],
                                           df_eventos['hora'],df_eventos['espelho_hora']))

  eventos_colaboradores[key] = df_eventos

In [5]:
matriculas = list(base_ficticia['matricula'])
datas = len(matriculas)*[date.today()]
lista_tempos_logados = [eventos_colaboradores[key]['tempo_logado'].sum() for key in eventos_colaboradores]
lista_tempos_produtivos = [eventos_colaboradores[key]['tempo_produtivo'].sum() for key in eventos_colaboradores]

df_resumo_jornada = pd.DataFrame({'data':datas,
                                  'matricula':matriculas,
                                  'tempo_logado':lista_tempos_logados,
                                  'tempo_produtivo':lista_tempos_produtivos
                                  })
df_resumo_jornada.head()

data  matricula  tempo_logado  tempo_produtivo
0  2023-03-27        912       68577.0          20888.0
1  2023-03-27        117       79443.0            564.0
2  2023-03-27        900       86399.0          86399.0
3  2023-03-27        899       66480.0          12622.0
4  2023-03-27        886       54779.0          20267.0

In [6]:
def converte_em_horas(segundos):
  horas = (pd.to_datetime('00:00')+timedelta(seconds=segundos)).time()

  return horas

df_resumo_jornada['tempo_logado'] = list(map(converte_em_horas,df_resumo_jornada['tempo_logado']))
df_resumo_jornada['tempo_produtivo'] = list(map(converte_em_horas,df_resumo_jornada['tempo_produtivo']))

In [7]:
df_resumo_jornada

data  matricula tempo_logado tempo_produtivo
0   2023-03-27        912     19:02:57        05:48:08
1   2023-03-27        117     22:04:03        00:09:24
2   2023-03-27        900     23:59:59        23:59:59
3   2023-03-27        899     18:28:00        03:30:22
4   2023-03-27        886     15:12:59        05:37:47
5   2023-03-27        325     19:22:12        00:56:08
6   2023-03-27        602     15:12:11        04:11:31
7   2023-03-27        210     14:57:33        06:14:02
8   2023-03-27        348     15:39:10        05:38:55
9   2023-03-27        901     13:20:43        00:09:28
10  2023-03-27        383     09:50:48        00:00:00
11  2023-03-27        561     18:27:46        05:39:45
12  2023-03-27        518     19:11:51        05:34:57
13  2023-03-27        401     14:46:38        05:15:32
14  2023-03-27        390     20:40:01        07:08:20
15  2023-03-27        940     05:45:10        00:00:00
16  2023-03-27        104     21:06:02        00:00:00
17  2023-03-27        718     13:24:29        05:06:55
18  2023-03-27        894     20:49:50        07:31:36
19  2023-03-27        753     12:39:39        03:33:29
20  2023-03-27        459     15:44:41        01:52:05
21  2023-03-27        237     12:31:26        05:46:05
22  2023-03-27        810     18:08:43        01:30:38
23  2023-03-27        760     17:32:58        03:58:27
24  2023-03-27        520     18:42:16        08:00:09
25  2023-03-27        691     16:13:15        04:53:23
26  2023-03-27        482     14:52:32        04:00:52
27  2023-03-27        398     17:28:39        01:20:51
28  2023-03-27        531     17:28:50        02:08:24
29  2023-03-27        871     19:04:59        05:58:12
30  2023-03-27        887     12:51:24        01:04:35
31  2023-03-27        412     23:59:59        23:59:59
32  2023-03-27        835     03:21:49        00:00:00
33  2023-03-27        697     07:57:18        00:00:00
34  2023-03-27        335     10:17:23        01:58:50
35  2023-03-27        751     13:35:01        03:18:03
36  2023-03-27        819     18:10:01        11:05:47
37  2023-03-27        274     14:08:03        01:20:15
38  2023-03-27        315     04:04:11        00:00:00
39  2023-03-27        756     23:59:59        23:59:59
40  2023-03-27        288     12:31:18        03:51:28
41  2023-03-27        547     17:09:25        08:34:10
42  2023-03-27        741     07:51:08        01:35:46
43  2023-03-27        329     17:17:16        06:41:19
44  2023-03-27        349     16:45:32        00:07:22
45  2023-03-27        830     06:04:47        00:00:00
46  2023-03-27        379     21:49:56        14:11:38
47  2023-03-27        700     08:39:19        00:00:00
48  2023-03-27        106     12:45:27        06:19:07
49  2023-03-27        690     16:15:39        10:43:13